In [4]:
##########################################################################################################################################
'''
    File name: expsim.ipynb
    File version: 2.0.0
    Created by: Caroline Karina Chandra
    Project: Advanced Research Lab (ARL), WiSe 20/21
    Date created: December 1, 2020
    Last modified: April 19, 2021
    Python version: 3.8
'''
##########################################################################################################################################
__author__     = "Caroline Karina Chandra"
__credits__    = ["Caroline Karina Chandra", "Imants Dirba"]
__maintainer__ = "Caroline Karina Chandra"
__contacts__   = ["caroline.k.chandra@gmail.com", "carolinekarina.chandra@stud.tu-darmstadt.de", "karin001207@yahoo.com"]
__version__    = "2.0.0"
__status__     = "Development"
##########################################################################################################################################

import ipywidgets as wg
from IPython.display import display
import matplotlib.pyplot as plt
from matplotlib.lines import Line2D
from matplotlib.offsetbox import AnchoredText
from ipywidgets import HBox, VBox, Checkbox, ToggleButton
from mpl_toolkits.mplot3d import Axes3D
from matplotlib import cm
from matplotlib.ticker import LinearLocator, FormatStrFormatter
%matplotlib widget
%run etc.ipynb

In [5]:
Material = wg.Text(value='Material', placeholder='Type material', disabled=False, layout=wg.Layout(width='100px', height='30px'))
Ku     = wg.BoundedFloatText(value=48, min=-430, max=6600, step=0.1, disabled=False, layout=wg.Layout(width='100px', height='25px'))
Kuout  = wg.Output()
Ms     = wg.BoundedFloatText(value=1711, min=1, max=2000, step=0.1, disabled=False, layout=wg.Layout(width='100px', height='25px'))
Msout  = wg.Output()
rho    = wg.BoundedFloatText(value=7.87, min=1e-3, max=1e3, step=1e-3, disabled=False, layout=wg.Layout(width='100px', height='25px'))
rhoout = wg.Output()
dpar   = wg.BoundedFloatText(value=9.95, min=1, max=60, step=0.01, disabled=False, layout=wg.Layout(width='100px', height='25px'))
dparout= wg.Output()

Medium = wg.Text(value='Medium', placeholder='Type medium', disabled=False, layout=wg.Layout(width='100px', height='30px'))
eta    = wg.BoundedFloatText(value=1e-3, min=1e-4, max=1e3, step=1e-4, disabled=False, layout=wg.Layout(width='100px', height='25px'))
etaout = wg.Output()
ds     = wg.BoundedFloatText(value=15, min=0, max=20, step=0.01, disabled=False, layout=wg.Layout(width='100px', height='25px'))
dsout  = wg.Output()

Mattext = wg.Label('Material :')
Kutext  = wg.Label(r'Anisotropy constant $K_u$ [kJ/m3] :')
Mstext  = wg.Label(r'Saturation magnetization $M_s$ [kA/m] :')
rhotext = wg.Label(r'Density of material $\rho$  [g/cm3] :')
dpartext= wg.Label(r'Particle diameter $d_p$ [nm] :')

space  = wg.Label(r'$\quad$')

Medtext= wg.Label('Medium :')
etatext= wg.Label(r'Viscosity $\eta$ [Ns/m2] :')
dstext  = wg.Label(r'Surfactant layer thickness $d_s$  [nm] :')

display(HBox((VBox((Mattext, Kutext, Mstext, rhotext, dpartext)),
              VBox((Material, Ku, Kuout, Ms, Msout, rho, rhoout, dpar, dparout)),
              space,
              VBox((Medtext, etatext, dstext)),
              VBox((Medium, eta, etaout, ds, dsout)) )) )

savebutton = wg.Button(description='Save', tooltip='The values saved will be used for further calculation')
saveout = wg.Output()
display(savebutton, saveout)

colorcode = ['b', 'g', 'r', 'm', 'k']


def on_button_clicked(save):
    with saveout:
        siKu  = float(Ku.value   * unit['Factor']['Anisotropy constant'])
        siMs  = float(Ms.value   * unit['Factor']['Saturation magnetization'])
        sirho = float(rho.value  * unit['Factor']['Density'])
        sieta = float(eta.value  * unit['Factor']['Viscosity'])
        sidp  = float(dpar.value * unit['Factor']['Surfactant layer thickness'])
        sids  = float(ds.value   * unit['Factor']['Surfactant layer thickness'])
        
        if sidp > ((6 * kb * T * np.log(1e50)) / (siKu * np.pi))**(1/3):
            maxdp = ((6 * kb * T * np.log(1e50)) / (siKu * np.pi))**(1/3)
            warningtext = wg.Label(f'Particle diameter exceeded maximum. Relaxation time has reached infinity.\n Max particle diameter for the given anisotropy constant is {round(maxdp * 1e9, 2)} nm')
            display(warningtext)
        else:
            tau_n = tau0 * ((siKu * np.pi * sidp**3) / (6 * kb * T))**(-0.5) * np.exp((siKu * np.pi * sidp**3) / (6 * kb * T))
#             tau_n = tau0 * np.exp((siKu * np.pi * sidp**3) / (6 * kb * T))
            tau_b = (sieta * np.pi * (sidp + sids)**3) / (2 * kb * T)
            tau_tot = (tau_n * tau_b) / (tau_n + tau_b)
#             fmax = 1 / (2 * np.pi * tau_tot)
#             print(f"fmax = {round(fmax / unit['Factor']['Frequency'])} kHz")
#             print(tau_tot)
            
            def plotdropdown(Axes):
                if Axes == 'select axes':
                    None
                elif Axes == 'frequency - SAR':
                    fieldtext = wg.Label('Field H [G] :', layout=wg.Layout(width='120px', height='30px'))
                    field0 = wg.BoundedIntText(value=100, min=1, max=500, disabled=False, layout=wg.Layout(width='70px'))
                    fieldout0 = wg.Output()
                    field1 = wg.BoundedIntText(value=0, min=0, max=500, disabled=False, layout=wg.Layout(width='70px'))
                    fieldout1 = wg.Output()
                    field2 = wg.BoundedIntText(value=0, min=0, max=500, disabled=False, layout=wg.Layout(width='70px'))
                    fieldout2 = wg.Output()
                    field3 = wg.BoundedIntText(value=0, min=0, max=500, disabled=False, layout=wg.Layout(width='70px'))
                    fieldout3 = wg.Output()
                    field4 = wg.BoundedIntText(value=0, min=0, max=500, disabled=False, layout=wg.Layout(width='70px'))
                    fieldout4 = wg.Output()
                    display(HBox((fieldtext, field0,fieldout0,field1,fieldout1,field2,fieldout2,field3,fieldout3,field4,fieldout4)))

                    saveff = wg.Button(description='Compute', tooltip='The values saved will be used for further calculation')
                    saveffout = wg.Output()
                    display(saveff, saveffout)
                    def on_button_clicked2(save2):
                        with saveffout:
                            
                            fields = [field0.value, field1.value, field2.value, field3.value, field4.value]

                            while 0 in fields:
                                fields.remove(0)
                            labels = [f'H = {fields[i]} G' for i in range(len(fields))]
                            fields = np.array(fields) * unit['Factor']['Field']

                            freqslider = wg.IntSlider(value=10, min=10, max=1000, description='f [kHz]')
                            fig, ax = plt.subplots()
                            ax.set_xlabel('f [kHz]')
                            ax.set_ylabel('SAR [W/g]')
#                             ax.add_artist(AnchoredText(f"{Material.value} \n{Medium.value}", loc=2))
                            ax.add_artist(AnchoredText(f"{Material.value} \n{Medium.value} \no $\leq$ Atkinson Limit \nx  > Atkinson Limit", loc='upper left'))                         
                            legend_elements = [Line2D([0], [0], marker='.', color=colorcode[i], linestyle='None', label=labels[i]) for i in range(len(fields))]
                            ax.legend(handles=legend_elements, loc='center left', fontsize=8)
#                             ax.set_yscale('log')
                            
                            
                            def freqSAR(freqslider):

                                for h in range(len(fields)):
                                    P = ((np.pi**3 * vacuumpermeability**2 * fields[h]**2 * siMs**2 * sidp**3 * (freqslider * unit['Factor']['Frequency'])**2 * tau_tot) / \
                                        (9 * kb * T * sirho * (1 + (2 * np.pi * freqslider * unit['Factor']['Frequency'] * tau_tot)**2))) * 1e-3
                                    if fields[h] * freqslider * unit['Factor']['Frequency'] <= 4.85e8:
                                        ax.scatter(freqslider, P, marker='o', s=15, color=colorcode[h])
                                    else:
                                        ax.scatter(freqslider, P, marker='x', s=10, color=colorcode[h])

                            wg.interact(freqSAR, freqslider=freqslider)
                            
                            x = np.arange(10, 1000, 1)
                            y = []
                            for h in range(len(fields)):
                                P = ((np.pi**3 * vacuumpermeability**2 * fields[h]**2 * siMs**2 * sidp**3 * (x * unit['Factor']['Frequency'])**2 * tau_tot) / \
                                     (9 * kb * T * sirho * (1 + (2 * np.pi * x * unit['Factor']['Frequency'] * tau_tot)**2))) * 1e-3
                                y.append(P)
                            X = np.array(x).reshape(len(x), 1)
                            Y = np.hstack(([np.array(y[h]).reshape(len(y[h]),1) for h in range(len(fields))]))

                            prefixSAR = ['SAR_' + i for i in labels]
                            Header = ['f', *prefixSAR]
                            
#                             print(Header)
                            export(X, Y, Material.value, Medium.value, Axes, Header)
                            
                    saveff.on_click(on_button_clicked2)
         
                elif Axes == 'field - SAR':
                    freqtext = wg.Label('Frequency f [kHz] :', layout=wg.Layout(width='120px', height='30px'))
                    freq0 = wg.BoundedIntText(value=100, min=1, max=500, disabled=False, layout=wg.Layout(width='70px'))
                    freqout0 = wg.Output()
                    freq1 = wg.BoundedIntText(value=0, min=0, max=500, disabled=False, layout=wg.Layout(width='70px'))
                    freqout1 = wg.Output()
                    freq2 = wg.BoundedIntText(value=0, min=0, max=500, disabled=False, layout=wg.Layout(width='70px'))
                    freqout2 = wg.Output()
                    freq3 = wg.BoundedIntText(value=0, min=0, max=500, disabled=False, layout=wg.Layout(width='70px'))
                    freqout3 = wg.Output()
                    freq4 = wg.BoundedIntText(value=0, min=0, max=500, disabled=False, layout=wg.Layout(width='70px'))
                    freqout4 = wg.Output()
                    display(HBox((freqtext, freq0,freqout0,freq1,freqout1,freq2,freqout2,freq3,freqout3,freq4,freqout4)))
                    
                    saveff = wg.Button(description='Compute', tooltip='The values saved will be used for further calculation')
                    saveffout = wg.Output()
                    display(saveff, saveffout)

                    
                    def on_button_clicked2(save2):
                        with saveffout:
                            freq = [freq0.value, freq1.value, freq2.value, freq3.value, freq4.value]

                            while 0 in freq:
                                freq.remove(0)
                            labels = [f'f = {freq[i]} kHz' for i in range(len(freq))]
                            freq = np.array(freq) * unit['Factor']['Frequency']
                            fieldslider = wg.IntSlider(value=10, min=10, max=1000, description='H [G]')
                            fig, ax = plt.subplots()
                            ax.set_xlabel('H [G]')
                            ax.set_ylabel('SAR [W/g]')
                            ax.add_artist(AnchoredText(f"{Material.value} \n{Medium.value} \no $\leq$ Atkinson Limit \nx  > Atkinson Limit", loc='upper left'))

                            legend_elements = [Line2D([0], [0], marker='.', color=colorcode[i], linestyle='None', label=labels[i]) for i in range(len(freq))]
                            ax.legend(handles=legend_elements, loc='center left', fontsize=8)
                            
                            
                            def fieldSAR(fieldslider):
#                                 print(f"field={fieldslider * unit['Factor']['Field']}, freq420={freq[0]}, Ms={siMs}, dp={sidp}, Ku={siKu}, eta={sieta}, rho={sirho}")
                                for f in range(len(freq)): 
                                    P = ((np.pi**3 * vacuumpermeability**2 * (fieldslider * unit['Factor']['Field'])**2 * siMs**2 * sidp**3 * freq[f]**2 * tau_tot) / \
                                         (9 * kb * T * sirho * (1 + (2 * np.pi * freq[f] * tau_tot)**2))) * 1e-3
                                    if fieldslider * freq[f] * unit['Factor']['Frequency'] <= 4.85e8:
                                        ax.scatter(fieldslider, P, marker='o', s=15, color=colorcode[f])
                                    else:
                                        ax.scatter(fieldslider, P, marker='x', s=10, color=colorcode[f])
                            wg.interact(fieldSAR, fieldslider=fieldslider)
                            
                            x = np.arange(10, 1000, 1)
                            y = []
                            for f in range(len(freq)):
                                P = ((np.pi**3 * vacuumpermeability**2 * (x * unit['Factor']['Field'])**2 * siMs**2 * sidp**3 * freq[f]**2 * tau_tot) / \
                                    (9 * kb * T * sirho * (1 + (2 * np.pi * freq[f] * tau_tot)**2))) * 1e-3
                                y.append(P)
                            X = np.array(x).reshape(len(x), 1)
                            Y = np.hstack(([np.array(y[h]).reshape(len(y[f]),1) for h in range(len(freq))]))
                            prefixSAR = ['SAR_' + i for i in labels]
                            Header = ['H', *prefixSAR]
                            export(X, Y, Material.value, Medium.value, Axes, Header)
                            
                    saveff.on_click(on_button_clicked2)
                elif Axes == 'f - H - SAR':
                    fig = plt.figure()
                    ax = fig.gca(projection='3d')
                    plt.tight_layout()
                    ax.set_xlabel('Frequency f [kHz]')
                    ax.set_ylabel('Field H [G]')
                    ax.set_zlabel('SAR [W/g]')
                    ax.invert_yaxis()
                    ax.view_init(elev=18, azim=-27)
                    ax.text2D(0.0, 0.98, f"{Material.value}, {Medium.value}", transform=ax.transAxes)
                    ax.text2D(0.0, 0.94, f"Ms: {Ms.value} kA/m, Ku: {Ku.value} kJ/m3, rho: {rho.value} g/cm3, eta: {eta.value} Ns/m2", transform=ax.transAxes, fontsize=8)
                    ax.text2D(0.0, 0.90, f"Particle diameter: {dpar.value} nm", transform=ax.transAxes, fontsize=8)
                    
                    # Make data.
                    X = np.arange(1, 500, 1) # f
                    Y = np.arange(1, 500, 1) # H
                    X, Y = np.meshgrid(X, Y)
                    Z = ((np.pi**3 * vacuumpermeability**2 * (Y * unit['Factor']['Field'])**2 * siMs**2 * sidp**3 * (X * unit['Factor']['Frequency'])**2 * tau_tot) / \
                        (9 * kb * T * sirho * (1 + (2 * np.pi * X * unit['Factor']['Frequency'] * tau_tot)**2))) * 1e-3

                    # Plot the surface.
                    surf = ax.plot_surface(X, Y, Z, cmap=cm.jet)#, rstride=1, cstride=1, linewidth=0, antialiased=False)
                    XYexport = np.hstack((np.array(X).reshape(np.shape(X)[0] * np.shape(X)[1], 1), np.array(Y).reshape(np.shape(Y)[0] * np.shape(Y)[1], 1)))
                    Zexport = np.hstack((np.array(Z).reshape(np.shape(Z)[0] * np.shape(Z)[1], 1), np.array(Z).reshape(np.shape(Z)[0] * np.shape(Z)[1], 1)))
                    Header = ['f', 'H', 'SAR', 'SAR (color)']
                    export(XYexport, Zexport, Material.value, None, f"{Axes} with dp: {dpar.value} nm", Header)
#                     print(Z)

    #####################################################################################################################################
                
#####################################################################################################################################
                        
            wg.interact(plotdropdown, Axes=simulation)
        
savebutton.on_click(on_button_clicked)


Button(description='Save', style=ButtonStyle(), tooltip='The values saved will be used for further calculation…

Output()

In [3]:
# print(np.exp(1e309))
# print(1.7975e308)
# print(np.log(1e308))
# print(np.exp(709))
# print(np.exp(710) / 1e305)
# print(np.exp(1e50))
# print(np.exp((48000 * np.pi * (27 * 1e-9)**3) / (6 * kb * T)))
# print(((48000 * np.pi * (27 * 1e-9)**3) / (6 * kb * T))**(-0.5) * 1e-9)
# print((48000 * np.pi * (27 * 1e-9)**3) / (6 * kb * T))

In [4]:
# # initializing list
# test_list = ['a', 'b', 'c', 'd']
  
# # printing list
# print("The original list : " + str(test_list))
  
# # initializing append_str
# append_str = 'gfg'
  
# # Append suffix / prefix to strings in list
# pre_res = [append_str + sub for sub in test_list]
# suf_res = [sub + append_str for sub in test_list]
  
# # Printing result
# print("list after prefix addition : " + str(pre_res))
# print("list after suffix addition : " + str(suf_res))